# Validate EIA-930 data against net generation outputs

In [30]:
import pandas as pd
import numpy as np
import os

import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [22]:
year = 2020

In [23]:
# EIA-930 data after timestamp adjustments but no cleaning
raw = pd.read_csv(f"../data/outputs/{year}/eia930/eia930_raw.csv", index_col=0, parse_dates=True)

In [14]:
GEN_ID = "EBA.{}-ALL.NG.H"
path = f"../data/results/{year}/power_sector_data/hourly/us_units/"
cors = {}
percent_difs = {}
annual_gen = {}
for ba_f in os.listdir(path):
    ba = ba_f.replace(".csv", "")
    print(ba, end="...")
    col_name = GEN_ID.format(ba)
    if col_name not in raw.columns: 
        continue
    else:
        dat = pd.read_csv(path+ba_f, parse_dates=["datetime_utc"])
        dat = dat[dat.fuel_category=="total"]
        dat = dat.merge(raw[ col_name], left_on="datetime_utc", right_index=True)
        c = dat[["net_generation_mwh", col_name]].corr().to_numpy()[0,1]
        cors[ba] = c
        difs = (dat[col_name]-dat["net_generation_mwh"])/dat["net_generation_mwh"]
        difs = difs.replace(np.inf, np.nan)
        percent_difs[ba] = difs.median()
        annual_gen[ba] = dat["net_generation_mwh"].sum()

OHMS...FMPP...ERCO...TPWR...AMPL...SOCO...IPCO...PJM...WWA...EEI...AZPS...TEC...DOPD...YAD...IID...HGMA...DEAA...CPLW...SPA...GVL...ORMS...FPL...TAL...SEC...JEA...GCPD...TVA...TIDC...HECO...SCEG...INMS...CPLE...SEPA...AKMS...CHPD...PNM...WAUW...WACM...WALC...NWMT...PACE...AVA...SC...NSB...GWA...HIMS...LGEE...TEPC...ISNE...SRP...GRIS...HST...LDWP...RIMS...FPC...PACW...GRIF...PSEI...AECI...CSTO...DUK...AVRN...CEA...MISO...AEC...PSCO...OVEC...SWPP...BANC...NYIS...EPE...NBSO...SCL...BPAT...NEVP...CISO...PGE...

In [5]:
out = pd.DataFrame(data={"Difference as percent of hourly-egrid":percent_difs, "Correlation":cors, "Annual BA generation":annual_gen})
out = out.sort_values("Annual BA generation", ascending=False)
out.to_csv(f"../data/results/{year}/validation_metrics/us_units/compare_930_hourlyegrid.csv")

NameError: name 'percent_difs' is not defined

# Visualize BA of interest

In [9]:
ba = "SWPP"
col_name = GEN_ID.format(ba)
dat = pd.read_csv(path+ba+".csv", parse_dates=["datetime_utc"])
dat = dat[dat.fuel_category=="total"]
dat = dat.merge(raw[ col_name], left_on="datetime_utc", right_index=True)

px.line(dat, x="datetime_utc", y=["net_generation_mwh", col_name])

In [23]:
residual_profiles = pd.read_csv(f"../data/outputs/{year}/residual_profiles_{year}.csv", parse_dates=["datetime_utc"])

In [24]:
toplot = residual_profiles[(residual_profiles.ba_code==ba) & (residual_profiles.fuel_category_eia930 =="natural_gas")]
px.line(toplot,x="datetime_utc", y="profile")

# Scrape Singularity emission and rate data 

* Drawbacks: 
    * won't have timestamp fix 
    * slow the first time (cache locally)

* Benefits: 
    * Don't have to re-do emission logic 

In [28]:
rate = pd.read_csv("../data/results/2020/power_sector_data/hourly/us_units/DEAA.csv", parse_dates=["datetime_utc"])
rate = rate[rate.fuel_category=="total"]

In [31]:
# Create figure with secondary y-axis
fig = make_subplots(specs=[[{"secondary_y": True}]])

# Add traces
fig.add_trace(
    go.Scatter(x=rate.datetime_utc, y=rate.generated_co2_rate_lb_per_mwh_for_electricity, name="Rate"),
    secondary_y=False,
)

fig.add_trace(
    go.Scatter(x=rate.datetime_utc, y=rate.net_generation_mwh, name="generation"),
    secondary_y=True,
)

fig.show()

In [32]:
cems = pd.read_csv("../data/results/2020/plant_data/hourly/us_units/CEMS_plant_data.csv", parse_dates=["datetime_utc"])
cems_orig = pd.read_csv("../data/outputs/2020/cems_2020.csv", parse_dates = ["datetime_utc"])

In [86]:
# 51 = a coal plant 
# 55282 = spiky NG plant 
plant_num = 55282
plant_of_interest = cems[cems.plant_id_eia==plant_num].copy()

In [87]:
plant_of_interest["heat_rate_mmbtu_mwh"] = plant_of_interest.fuel_consumed_for_electricity_mmbtu/plant_of_interest.net_generation_mwh
plant_of_interest["emission_rate_co2_mmbtu"] = plant_of_interest.co2_mass_lb_for_electricity/plant_of_interest.fuel_consumed_for_electricity_mmbtu

In [88]:
px.line(plant_of_interest, x="datetime_utc", y="emission_rate_co2_mmbtu")

In [89]:
plant_of_interest.head()

plant_id_eia              datetime_utc report_date  \
7228250         55282 2020-01-01 07:00:00+00:00  2020-01-01   
7228251         55282 2020-01-01 08:00:00+00:00  2020-01-01   
7228252         55282 2020-01-01 09:00:00+00:00  2020-01-01   
7228253         55282 2020-01-01 10:00:00+00:00  2020-01-01   
7228254         55282 2020-01-01 11:00:00+00:00  2020-01-01   

         net_generation_mwh  fuel_consumed_mmbtu  \
7228250              492.44               3479.2   
7228251              493.41               3486.9   
7228252              493.41               3484.6   
7228253              494.37               3488.1   
7228254              493.41               3486.8   

         fuel_consumed_for_electricity_mmbtu  co2_mass_lb  ch4_mass_lb  \
7228250                               3479.2     413600.0         7.65   
7228251                               3486.9     414600.0         7.67   
7228252                               3484.6     414200.0         7.67   
7228253                               3488.1     414600.0         7.67   
7228254                               3486.8     414400.0         7.67   

         n2o_mass_lb  co2e_mass_lb  ...  nox_mass_lb_adjusted  \
7228250         0.77     414088.34  ...                 24.35   
7228251         0.77     415089.42  ...                 24.41   
7228252         0.77     414689.10  ...                 24.39   
7228253         0.77     415089.59  ...                 24.42   
7228254         0.77     414889.41  ...                 24.41   

         so2_mass_lb_adjusted  co2_mass_lb_for_electricity_adjusted  \
7228250                  2.09                              413600.0   
7228251                  2.09                              414600.0   
7228252                  2.09                              414200.0   
7228253                  2.09                              414600.0   
7228254                  2.09                              414400.0   

         ch4_mass_lb_for_electricity_adjusted  \
7228250                                  7.65   
7228251                                  7.67   
7228252                                  7.67   
7228253                                  7.67   
7228254                                  7.67   

         n2o_mass_lb_for_electricity_adjusted  \
7228250                                  0.77   
7228251                                  0.77   
7228252                                  0.77   
7228253                                  0.77   
7228254                                  0.77   

         co2e_mass_lb_for_electricity_adjusted  \
7228250                              414088.34   
7228251                              415089.42   
7228252                              414689.10   
7228253                              415089.59   
7228254                              414889.41   

         nox_mass_lb_for_electricity_adjusted  \
7228250                                 24.35   
7228251                                 24.41   
7228252                                 24.39   
7228253                                 24.42   
7228254                                 24.41   

         so2_mass_lb_for_electricity_adjusted  heat_rate_mmbtu_mwh  \
7228250                                  2.09             7.065226   
7228251                                  2.09             7.066942   
7228252                                  2.09             7.062281   
7228253                                  2.09             7.055647   
7228254                                  2.09             7.066740   

         emission_rate_co2_mmbtu  
7228250               118.877903  
7228251               118.902177  
7228252               118.865867  
7228253               118.861271  
7228254               118.848228  

[5 rows x 32 columns]

In [90]:
plant_of_interest_orig = cems_orig[cems_orig.plant_id_eia==plant_num]

In [91]:
# Create figure with secondary y-axis
from matplotlib.pyplot import title


fig = make_subplots(specs=[[{"secondary_y": True}]])

# Add traces
fig.add_trace(
    go.Scatter(x=plant_of_interest.datetime_utc, y=plant_of_interest.co2_mass_lb, name="CO2 emissions"),
    secondary_y=False,
)

fig.add_trace(
    go.Scatter(x=plant_of_interest_orig.datetime_utc, y=plant_of_interest_orig.gross_generation_mwh, name="gross generation"),
    secondary_y=True,
)

fig.update_layout(
    title=f"Plant {plant_num} generation vs. emissions"
)

fig.show()

In [53]:
plant_meta = pd.read_csv("../data/results/2020/plant_data/plant_static_attributes.csv")

In [59]:
plant_meta[plant_meta.plant_id_eia==55282]

Unnamed: 0  plant_id_eia plant_primary_fuel data_availability ba_code  \
3843        3843         55282                 NG      cems_and_eia    DEAA   

     ba_code_physical state distribution_flag fuel_category  \
3843              SRP    AZ             False   natural_gas   

     fuel_category_eia930         timezone  
3843          natural_gas  America/Phoenix

In [78]:
cems_orig[(cems_orig.gross_generation_mwh <= 2) & (cems_orig.gross_generation_mwh > 0)]

plant_id_eia  subplant_id              datetime_utc report_date  \
631                  3          0.0 2020-01-27 13:00:00+00:00  2020-01-01   
2071                 3          1.0 2020-01-27 13:00:00+00:00  2020-01-01   
8581                 3          3.0 2020-03-24 18:00:00+00:00  2020-03-01   
9982                 3          3.0 2020-05-22 03:00:00+00:00  2020-05-01   
19901                3          4.0 2020-07-08 10:00:00+00:00  2020-07-01   
...                ...          ...                       ...         ...   
21580076         61242          1.0 2020-08-12 21:00:00+00:00  2020-08-01   
21580081         61242          1.0 2020-08-13 02:00:00+00:00  2020-08-01   
21580194         61242          1.0 2020-08-17 19:00:00+00:00  2020-08-01   
21580225         61242          1.0 2020-08-19 02:00:00+00:00  2020-08-01   
21580311         61242          1.0 2020-08-22 16:00:00+00:00  2020-08-01   

          gross_generation_mwh  steam_load_1000_lb  fuel_consumed_mmbtu  \
631                       2.00                 0.0           224.800003   
2071                      0.50                 0.0            17.231251   
8581                      1.00                 0.0           417.799988   
9982                      1.00                 0.0           401.899994   
19901                     0.50                 0.0            89.250000   
...                        ...                 ...                  ...   
21580076                  0.50                 0.0             1.249000   
21580081                  0.84                 0.0             2.023200   
21580194                  1.30                 0.0             2.720900   
21580225                  1.82                 0.0             3.096080   
21580311                  0.72                 0.0             1.781280   

           co2_mass_lb  ch4_mass_lb  n2o_mass_lb  ...  \
631       26800.000000     0.494560     0.049456  ...   
2071       2050.000000     0.037909     0.003791  ...   
8581      85800.000000    10.131650     1.474834  ...   
9982      82400.000000     9.746075     1.418707  ...   
19901     10600.000000     0.196350     0.019635  ...   
...                ...          ...          ...  ...   
21580076    148.000000     0.002748     0.000275  ...   
21580081    239.039993     0.004451     0.000445  ...   
21580194    324.480011     0.005986     0.000599  ...   
21580225    368.420013     0.006811     0.000681  ...   
21580311    213.119995     0.003919     0.000392  ...   

          n2o_mass_lb_for_electricity  n2o_mass_lb_for_electricity_adjusted  \
631                          0.049456                              0.049456   
2071                         0.003791                              0.003791   
8581                         1.474834                              1.474834   
9982                         1.418707                              1.418707   
19901                        0.019635                              0.019635   
...                               ...                                   ...   
21580076                     0.000275                              0.000275   
21580081                     0.000445                              0.000445   
21580194                     0.000599                              0.000599   
21580225                     0.000681                              0.000681   
21580311                     0.000392                              0.000392   

          nox_mass_lb_for_electricity  nox_mass_lb_for_electricity_adjusted  \
631                          8.801000                              8.801000   
2071                         0.674750                              0.674750   
8581                        48.000000                             48.000000   
9982                        38.599998                             38.599998   
19901                       10.900000                             10.900000   
...                               ...                                   ... 